In [71]:
import subprocess
import os
import pandas as pd
import geopandas as gpd
import numpy as np
from shapely.geometry import Point
import matplotlib.pyplot as plt
import folium
import branca.colormap as cm
from tqdm import tqdm
from rtree import index

In [72]:
def get_git_root():
    try:
        root_dir = (
            subprocess.check_output(["git", "rev-parse", "--show-toplevel"])
            .strip()
            .decode("utf-8")
        )
        return root_dir
    except subprocess.CalledProcessError:
        raise Exception("This is not a Git repository")


# Get the Git repository's root directory
repo_root = get_git_root()
subfolder='data'
file_path = os.path.join(repo_root, subfolder, "SNGE8RFL.shp")
gps_df=gpd.read_file(file_path)

In [73]:
###Calculate the wealth index average for each cluster with weights based on the household sample weight
household_wealth_index_df=pd.read_csv(os.path.join(repo_root, "Wealth_Index_DF.csv"))
def weighted_average(values, weights):
    return np.average(values, weights=weights) 

cluster_wealth=household_wealth_index_df.groupby('hv001').apply(
    lambda x:pd.Series({'wealth_index':weighted_average(x['wealth_index'],x['hv005'])})
).reset_index()

C:\Users\worbo\AppData\Local\Temp\ipykernel_11800\1627577868.py:6: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  cluster_wealth=household_wealth_index_df.groupby('hv001').apply(


In [74]:
gps_dfmerged=pd.merge(gps_df, cluster_wealth,left_on='DHSCLUST',right_on='hv001',how='right') #Adding the wealth index to the gps data


In [75]:
senegal_filepath=os.path.join(repo_root, subfolder,'Senegal_Shapefile', "gadm41_SEN_0.shp")
senegal_boundary=gpd.read_file(senegal_filepath)

In [76]:
###Creating the geometry and the dataframe that includes the geometry
geometry=[Point(xy) for xy in zip(gps_dfmerged['LONGNUM'],gps_dfmerged['LATNUM'])]
gdf=gpd.GeoDataFrame(gps_dfmerged,geometry=geometry)
senegal_boundary = senegal_boundary.to_crs(gdf.crs)
gdf = gdf.to_crs(epsg=32628)###Converting to UTM for buffer creation

###adding a buffer based on ubran or rural
def create_errorbounds(row):
    if row["URBAN_RURA"]=='U':
        return row['geometry'].buffer(2000)
    elif row["URBAN_RURA"]=='R':
        return row['geometry'].buffer(5050)
    else:
        print(f"Error, can't determine urban or rural for row {row}. Exiting")
        exit()

gdf['buffer']=gdf.apply(create_errorbounds,axis=1)
buffer_gdf = gpd.GeoDataFrame(gdf[["buffer"]], geometry="buffer", crs="EPSG:32628")
buffer_gdf = buffer_gdf.to_crs(epsg=4326)
gdf["buffer"] = buffer_gdf["buffer"]
gdf['buffer']=gdf['buffer'].to_crs(epsg=4326)###Converting back to WGS84 for plotting
gdf = gdf.to_crs(epsg=4326)###Converting back to WGS84 for plotting

###Clipping the buffer to the Senegal boundary
gdf_clipped=gdf['buffer'].clip(senegal_boundary)
gdf['buffer']=gdf_clipped
###For overlapping regions, averaging the wealth index
gdf['wealth_index']=gdf.groupby('buffer')['wealth_index'].transform('mean')
gdf = gdf.drop(columns=["geometry"])
# Drop duplicates in household_wealth_index to ensure each hv001 has only one hv005
household_wealth_index_unique = household_wealth_index_df[['hv001', 'hv005']].drop_duplicates(subset='hv001')

# Merge the DataFrames on the matching columns
merged_df = gdf.merge(household_wealth_index_unique, left_on='DHSCLUST', right_on='hv001', how='left')

# Update the hv005 column in gdf with the corresponding values from household_wealth_index
gdf['hv005'] = merged_df['hv005']

# Drop the extra columns added during the merge
gdf.drop(columns=['hv001'], inplace=True)
gdf.set_geometry("buffer", inplace=True)

In [35]:
###TODO: Ensure this is correctly handling multiple overlaps

In [77]:
def handle_overlaps(gdf, column):
    total_geometries = len(gdf)  # Track total number of geometries
    progress_bar = tqdm(total=total_geometries, desc="Processing overlaps")

    while True:
        new_rows = []
        processed = set()  # Track processed indices

        # Create an R-tree spatial index for faster intersection checks
        spatial_index = index.Index()
        for i, geom in enumerate(gdf.geometry):
            if not geom.is_empty:
                spatial_index.insert(i, geom.bounds)

        for idx, row in gdf.iterrows():
            if idx in processed or row["buffer"].is_empty:
                continue  # Skip if already processed or empty

            # Find possible overlaps using the spatial index
            possible_overlaps = list(spatial_index.intersection(row["buffer"].bounds))
            
            for jdx in possible_overlaps:
                if idx >= jdx or jdx in processed:
                    continue  # Skip duplicates and processed geometries

                geo1 = row["buffer"]
                geo2 = gdf.at[jdx, "buffer"]
                intersection = geo1.intersection(geo2)

                if not intersection.is_empty:
                    # Compute weighted average
                    weight1 = row['hv005']
                    weight2 = gdf.at[jdx, 'hv005']
                    total_weight = weight1 + weight2
                    avg_val = (row[column] * weight1 + gdf.at[jdx, column] * weight2) / total_weight

                    # Create new row for the intersection
                    new_row = row.copy()
                    new_row["buffer"] = intersection
                    new_row[column] = avg_val
                    new_rows.append(new_row)

                    # Adjust original geometries
                    gdf.at[idx, "buffer"] = geo1.difference(intersection)
                    gdf.at[jdx, "buffer"] = geo2.difference(intersection)

                    # Mark as processed
                    processed.add(idx)
                    processed.add(jdx)

            progress_bar.update(1)  # Update progress

        # Stop if no new intersections were found
        if not new_rows:
            break

        # Add new rows and filter empty geometries
        new_gdf = gpd.GeoDataFrame(new_rows, geometry="buffer", crs=gdf.crs)
        gdf = pd.concat([gdf, new_gdf], ignore_index=True)
        gdf = gdf[gdf["buffer"].is_empty == False]

    progress_bar.close()
    return gdf


# Assuming your GeoDataFrame is named 'gdf' and the column to average is 'wealth_index'
gdf_averaged = handle_overlaps(gdf, "wealth_index")

Processing overlaps: 600it [00:00, 1381.55it/s]                         

KeyError: 534

Processing overlaps: 600it [00:20, 1381.55it/s]

In [61]:
fig, ax = plt.subplots(figsize=(10, 10),dpi=1000)

# Plot Senegal boundary
senegal_boundary.plot(ax=ax, color="lightgray", edgecolor="black")

gdf_averaged.plot(
    column="wealth_index",
    ax=ax,
    legend=True,
    legend_kwds={"label": "Average Wealth Index", "orientation": "horizontal"},
    edgecolor="none",
    cmap='RdYlBu_r'
)

plt.title("Averaged Wealth Index Across Senegal")
plt.xlabel("Longitude")
plt.ylabel("Latitude")
plt.show()

In [62]:
# Create a base map centered around Senegal
m = folium.Map(location=[14.4974, -14.4524], zoom_start=6)

# Create a colormap
colormap = cm.linear.Blues_09.scale(
    gdf_averaged["wealth_index"].min(), gdf_averaged["wealth_index"].max()
)
colormap = cm.LinearColormap(
    colors=["blue", "red"],
    vmin=gdf_averaged["wealth_index"].min(),
    vmax=gdf_averaged["wealth_index"].max(),
)
colormap.caption = "Wealth Index"


# Function to style the GeoJson features
def style_function(feature):
    return {
        "fillColor": colormap(feature["properties"]["wealth_index"]),
        'color':'none',
        "weight": 0,
        "fillOpacity": 0.7,
    }


# Add the GeoDataFrame to the map
folium.GeoJson(
    gdf_averaged,
    style_function=style_function,
    tooltip=folium.GeoJsonTooltip(fields=["wealth_index"], aliases=["Wealth Index:"]),
).add_to(m)

# Add the colormap to the map
colormap.add_to(m)

# Save the map to an HTML file
m.save("senegal_wealth_index_map.html")

# Display the map in a Jupyter Notebook
m

c:\Users\worbo\anaconda3\envs\py12.7seminar\Lib\site-packages\folium\features.py:1156: UserWarning: GeoJsonTooltip is not configured to render for GeoJson GeometryCollection geometries. Please consider reworking these features: [{'DHSID': 'SN202300000103', 'DHSCC': 'SN', 'DHSYEAR': 2023.0, 'DHSCLUST': 103.0, 'CCFIPS': 'SG', 'ADM1FIPS': 'NULL', 'ADM1FIPSNA': 'NULL', 'ADM1SALBNA': 'NULL', 'ADM1SALBCO': 'NULL', 'ADM1DHS': 4.0, 'ADM1NAME': 'Saint-Louis', 'DHSREGCO': 4.0, 'DHSREGNA': 'Saint-Louis', 'SOURCE': 'CEN', 'URBAN_RURA': 'U', 'LATNUM': 16.454359773, 'LONGNUM': -15.678726626, 'ALT_GPS': 9999.0, 'ALT_DEM': 10.0, 'DATUM': 'WGS84', 'wealth_index': 1.0360984863414886, 'hv005': 588049.0}, {'DHSID': 'SN202300000006', 'DHSCC': 'SN', 'DHSYEAR': 2023.0, 'DHSCLUST': 6.0, 'CCFIPS': 'SG', 'ADM1FIPS': 'NULL', 'ADM1FIPSNA': 'NULL', 'ADM1SALBNA': 'NULL', 'ADM1SALBCO': 'NULL', 'ADM1DHS': 1.0, 'ADM1NAME': 'Dakar', 'DHSREGCO': 1.0, 'DHSREGNA': 'Dakar', 'SOURCE': 'CEN', 'URBAN_RURA': 'U', 'LATNUM': 14.

In [11]:
gdf_averaged.to_csv(os.path.join(repo_root, subfolder, "Senegal_Wealth_Index.csv"), index=False)